# NCI-Deepmind GraphCast-02

In [1]:
# @title Imports

import dataclasses
import datetime
import functools
import math
import re
from typing import Optional

import cartopy.crs as ccrs
from google.cloud import storage
from graphcast import autoregressive
from graphcast import casting
from graphcast import checkpoint
from graphcast import data_utils
from graphcast import graphcast
from graphcast import normalization
from graphcast import rollout
from graphcast import xarray_jax
from graphcast import xarray_tree
from IPython.display import HTML
import ipywidgets as widgets
import haiku as hk
import jax
import matplotlib
import matplotlib.pyplot as plt
from matplotlib import animation
import numpy as np
import xarray
from dask.diagnostics import ProgressBar
import os
from tqdm.std import tqdm

def parse_file_parts(file_name):
  return dict(part.split("-", 1) for part in file_name.split("_"))


dl_dir = '/g/data/wb00/admin/testing/graphcast/'
from os import listdir
from os.path import isfile, join


In [2]:
%%time
from pathlib import Path
import hashlib
#os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = r"/scratch/fp0/mah900/graphcast/nci-2023-01-22c2d43b7789.json"
bucket_name = "dm_graphcast"

dl_dir = '/g/data/wb00/admin/testing/graphcast/'
storage_client = storage.Client.create_anonymous_client()
bucket         = storage_client.get_bucket("dm_graphcast")
#storage_client = storage.Client()
#blobs_list     = bucket.list_blobs(""))
#for file in file_list:
#    print (file.name)
file_list = storage_client.list_blobs(bucket_name)
for blob in file_list:
    print ("Blob:", blob.name+",", "Size:", str(round(blob.size/(2**30),2) )+"GB,", "Md5_hash:",  blob.md5_hash )
    if blob.name.endswith("/"):
        continue
    file_split = blob.name.split("/")
    directory  = "/".join(file_split[0:-1])
    filename   = file_split[-1]
    Path(dl_dir + directory).mkdir(parents=True, exist_ok=True)
    destination_file_name = dl_dir + directory + "/" + filename
    
    if os.path.isfile(destination_file_name):
        print("Destination file exists: ", destination_file_name)
        print()
        continue
        
    print(destination_file_name)
    with open(destination_file_name, 'wb') as f:
        with tqdm.wrapattr(f, "write", total=blob.size, miniters=blob.size/100) as file_obj:
            storage_client.download_blob_to_file(blob, file_obj)
    #blob.download_to_filename(dl_dir + directory + "/" + filename) 
    #print(hashlib.md5(open(destination_file_name,'rb').read()).hexdigest())
    print()

#gcs_client = storage.Client.create_anonymous_client()
#gcs_bucket = gcs_client.get_bucket("dm_graphcast")

Blob: dataset/source-era5_date-2022-01-01_res-0.25_levels-13_steps-01.nc, Size: 0.98GB, Md5_hash: uue+jAi9QokoQ2A4ORbSDA==
Destination file exists:  /g/data/wb00/admin/testing/graphcast/dataset/source-era5_date-2022-01-01_res-0.25_levels-13_steps-01.nc

Blob: dataset/source-era5_date-2022-01-01_res-0.25_levels-13_steps-04.nc, Size: 1.96GB, Md5_hash: y1VEYF1Up43Rdjzibtzrsw==
Destination file exists:  /g/data/wb00/admin/testing/graphcast/dataset/source-era5_date-2022-01-01_res-0.25_levels-13_steps-04.nc

Blob: dataset/source-era5_date-2022-01-01_res-0.25_levels-13_steps-12.nc, Size: 4.56GB, Md5_hash: o4Alk7EXrcQeDCWkSfBl0A==
Destination file exists:  /g/data/wb00/admin/testing/graphcast/dataset/source-era5_date-2022-01-01_res-0.25_levels-13_steps-12.nc

Blob: dataset/source-era5_date-2022-01-01_res-0.25_levels-37_steps-01.nc, Size: 2.65GB, Md5_hash: tBIMMxpZKlmea4Cav6TB5Q==
Destination file exists:  /g/data/wb00/admin/testing/graphcast/dataset/source-era5_date-2022-01-01_res-0.25_levels-

In [3]:
# @title Plotting functions

def select(
    data: xarray.Dataset,
    variable: str,
    level: Optional[int] = None,
    max_steps: Optional[int] = None
    ) -> xarray.Dataset:
  data = data[variable]
  if "batch" in data.dims:
    data = data.isel(batch=0)
  if max_steps is not None and "time" in data.sizes and max_steps < data.sizes["time"]:
    data = data.isel(time=range(0, max_steps))
  if level is not None and "level" in data.coords:
    data = data.sel(level=level)
  return data

def scale(
    data: xarray.Dataset,
    center: Optional[float] = None,
    robust: bool = False,
    ) -> tuple[xarray.Dataset, matplotlib.colors.Normalize, str]:
  vmin = np.nanpercentile(data, (2 if robust else 0))
  vmax = np.nanpercentile(data, (98 if robust else 100))
  if center is not None:
    diff = max(vmax - center, center - vmin)
    vmin = center - diff
    vmax = center + diff
  return (data, matplotlib.colors.Normalize(vmin, vmax),
          ("RdBu_r" if center is not None else "viridis"))

def plot_data(
    data: dict[str, xarray.Dataset],
    fig_title: str,
    plot_size: float = 5,
    robust: bool = False,
    cols: int = 4
    ) -> tuple[xarray.Dataset, matplotlib.colors.Normalize, str]:

  first_data = next(iter(data.values()))[0]
  max_steps = first_data.sizes.get("time", 1)
  assert all(max_steps == d.sizes.get("time", 1) for d, _, _ in data.values())

  cols = min(cols, len(data))
  rows = math.ceil(len(data) / cols)
  figure = plt.figure(figsize=(plot_size * 2 * cols,
                               plot_size * rows))
  figure.suptitle(fig_title, fontsize=16)
  figure.subplots_adjust(wspace=0, hspace=0)
  figure.tight_layout()

  images = []
  for i, (title, (plot_data, norm, cmap)) in enumerate(data.items()):
    ax = figure.add_subplot(rows, cols, i+1)
    ax.set_xticks([])
    ax.set_yticks([])
    ax.set_title(title)
    im = ax.imshow(
        plot_data.isel(time=0, missing_dims="ignore"), norm=norm,
        origin="lower", cmap=cmap)
    plt.colorbar(
        mappable=im,
        ax=ax,
        orientation="vertical",
        pad=0.02,
        aspect=16,
        shrink=0.75,
        cmap=cmap,
        extend=("both" if robust else "neither"))
    images.append(im)

  def update(frame):
    if "time" in first_data.dims:
      td = datetime.timedelta(microseconds=first_data["time"][frame].item() / 1000)
      figure.suptitle(f"{fig_title}, {td}", fontsize=16)
    else:
      figure.suptitle(fig_title, fontsize=16)
    for im, (plot_data, norm, cmap) in zip(images, data.values()):
      im.set_data(plot_data.isel(time=frame, missing_dims="ignore"))

  ani = animation.FuncAnimation(
      fig=figure, func=update, frames=max_steps, interval=250)
  plt.close(figure.number)
  return HTML(ani.to_jshtml())

In [4]:
# @title Choose the model

#params_file_options = [
#    name for blob in gcs_bucket.list_blobs(prefix="params/")
#    if (name := blob.name.removeprefix("params/"))]  # Drop empty string.
params_file_options = [f for f in listdir(dl_dir+"params/") if isfile(join(dl_dir+"params/", f))]

random_mesh_size = widgets.IntSlider(
    value=4, min=4, max=6, description="Mesh size:")
random_gnn_msg_steps = widgets.IntSlider(
    value=4, min=1, max=32, description="GNN message steps:")
random_latent_size = widgets.Dropdown(
    options=[int(2**i) for i in range(4, 10)], value=32,description="Latent size:")
random_levels = widgets.Dropdown(
    options=[13, 37], value=13, description="Pressure levels:")


params_file = widgets.Dropdown(
    options=params_file_options,
    description="Params file:",
    layout={"width": "max-content"})

source_tab = widgets.Tab([
    params_file,
    widgets.VBox([
        random_mesh_size,
        random_gnn_msg_steps,
        random_latent_size,
        random_levels,
    ]),
    #params_file,
])
#source_tab.set_title(0, "Random")
#source_tab.set_title(1, "Checkpoint")
source_tab.set_title(1, "Random")
source_tab.set_title(0, "Checkpoint")
widgets.VBox([
    source_tab,
    widgets.Label(value="Run the next cell to load the model. Rerunning this cell clears your selection.")
])

     

In [5]:
%%time
# @title Load the model
from tqdm.std import tqdm
source = source_tab.get_title(source_tab.selected_index)

if source == "Random":
  params = None  # Filled in below
  state = {}
  model_config = graphcast.ModelConfig(
      resolution=0,
      mesh_size=random_mesh_size.value,
      latent_size=random_latent_size.value,
      gnn_msg_steps=random_gnn_msg_steps.value,
      hidden_layers=1,
      radius_query_fraction_edge_length=0.6)
  task_config = graphcast.TaskConfig(
      input_variables=graphcast.TASK.input_variables,
      target_variables=graphcast.TASK.target_variables,
      forcing_variables=graphcast.TASK.forcing_variables,
      pressure_levels=graphcast.PRESSURE_LEVELS[random_levels.value],
      input_duration=graphcast.TASK.input_duration,
  )
else:
  assert source == "Checkpoint"
  #with gcs_bucket.blob(f"params/{params_file.value}").open("rb") as f:
  with open(dl_dir + "params/" + str(params_file.value), "rb") as f:
      ckpt = checkpoint.load(f, graphcast.CheckPoint)
      #with tqdm.wrapattr( f, "write", total=gcs_bucket.blob(f"params/{params_file.value}").size ) as file_obj:       
      #    ckpt = checkpoint.load(file_obj, graphcast.CheckPoint)
  params = ckpt.params
  state = {}

  model_config = ckpt.model_config
  task_config = ckpt.task_config
  print("Model description:\n", ckpt.description, "\n")
  print("Model license:\n", ckpt.license, "\n")

model_config

Model description:
 
GraphCast model at 0.25deg resolution, with 37 pressure levels. This model is
trained on ERA5 data from 1979 to 2017, and can be causally evaluated on 2018
and later years. This model takes as inputs `total_precipitation_6hr`. This was
described in the paper
`GraphCast: Learning skillful medium-range global weather forecasting`
(https://arxiv.org/abs/2212.12794).
 

Model license:
 
The model weights are licensed under the Creative Commons
Attribution-NonCommercial-ShareAlike 4.0 International (CC BY-NC-SA 4.0). You
may obtain a copy of the License at:
https://creativecommons.org/licenses/by-nc-sa/4.0/.
The weights were trained on ERA5 data, see README for attribution statement.
 

CPU times: user 252 ms, sys: 133 ms, total: 385 ms
Wall time: 732 ms


ModelConfig(resolution=0.25, mesh_size=6, latent_size=512, gnn_msg_steps=16, hidden_layers=1, radius_query_fraction_edge_length=0.5999912857713345, mesh2grid_edge_normalization_factor=0.6180338738074472)

In [6]:
%%time
# @title Get and filter the list of available example datasets

#dataset_file_options = [
#    name for blob in gcs_bucket.list_blobs(prefix="dataset/")
#    if (name := blob.name.removeprefix("dataset/"))]  # Drop empty string.
dataset_file_options = [f for f in listdir(dl_dir+"dataset/") if isfile(join(dl_dir+"dataset/", f))]

def data_valid_for_model(
    file_name: str, model_config: graphcast.ModelConfig, task_config: graphcast.TaskConfig):
  file_parts = parse_file_parts(file_name.removesuffix(".nc"))
  return (
      model_config.resolution in (0, float(file_parts["res"])) and
      len(task_config.pressure_levels) == int(file_parts["levels"]) and
      (
          ("total_precipitation_6hr" in task_config.input_variables and
           file_parts["source"] in ("era5", "fake")) or
          ("total_precipitation_6hr" not in task_config.input_variables and
           file_parts["source"] in ("hres", "fake"))
      )
  )


dataset_file = widgets.Dropdown(
    options=[
        (", ".join([f"{k}: {v}" for k, v in parse_file_parts(option.removesuffix(".nc")).items()]), option)
        for option in dataset_file_options
        if data_valid_for_model(option, model_config, task_config)
    ][::-1],
    description="Dataset file:",
    layout={"width": "max-content"})
widgets.VBox([
    dataset_file,
    widgets.Label(value="Run the next cell to load the dataset. Rerunning this cell clears your selection and refilters the datasets that match your model.")
])
   

CPU times: user 4.68 ms, sys: 0 ns, total: 4.68 ms
Wall time: 4.24 ms


In [7]:
%%time
# @title Load weather data
#from dask.diagnostics import ProgressBar

if not data_valid_for_model(dataset_file.value, model_config, task_config):
  raise ValueError(
      "Invalid dataset file, rerun the cell above and choose a valid dataset file.")

#with gcs_bucket.blob(f"dataset/{dataset_file.value}").open("rb") as f:
with open(dl_dir + "dataset/" + str(dataset_file.value), "rb") as f:    
    #with ProgressBar():
      example_batch = xarray.load_dataset(f).compute()

assert example_batch.dims["time"] >= 3  # 2 for input, >=1 for targets

print(", ".join([f"{k}: {v}" for k, v in parse_file_parts(dataset_file.value.removesuffix(".nc")).items()]))

example_batch

source: era5, date: 2022-01-01, res: 0.25, levels: 37, steps: 12
CPU times: user 4.16 s, sys: 18.3 s, total: 22.4 s
Wall time: 33.6 s


<xarray.Dataset>
Dimensions:                       (lon: 1440, lat: 721, level: 37, time: 14,
                                   batch: 1)
Coordinates:
  * lon                           (lon) float32 0.0 0.25 0.5 ... 359.5 359.8
  * lat                           (lat) float32 -90.0 -89.75 ... 89.75 90.0
  * level                         (level) int32 1 2 3 5 7 ... 925 950 975 1000
  * time                          (time) timedelta64[ns] 0 days 00:00:00 ... ...
    datetime                      (batch, time) datetime64[ns] 2022-01-01 ......
Dimensions without coordinates: batch
Data variables: (12/14)
    geopotential_at_surface       (lat, lon) float32 2.735e+04 ... -0.07617
    land_sea_mask                 (lat, lon) float32 1.0 1.0 1.0 ... 0.0 0.0 0.0
    2m_temperature                (batch, time, lat, lon) float32 250.7 ... 2...
    mean_sea_level_pressure       (batch, time, lat, lon) float32 9.931e+04 ....
    10m_v_component_of_wind       (batch, time, lat, lon) float32 -0.4393 ......
    10m_u_component_of_wind       (batch, time, lat, lon) float32 1.309 ... -...
    ...                            ...
    temperature                   (batch, time, level, lat, lon) float32 286....
    geopotential                  (batch, time, level, lat, lon) float32 4.93...
    u_component_of_wind           (batch, time, level, lat, lon) float32 -0.0...
    v_component_of_wind           (batch, time, level, lat, lon) float32 -0.0...
    vertical_velocity             (batch, time, level, lat, lon) float32 -0.0...
    specific_humidity             (batch, time, level, lat, lon) float32 3.91...

In [8]:
%%time
# @title Choose data to plot

plot_example_variable = widgets.Dropdown(
    options=example_batch.data_vars.keys(),
    value="2m_temperature",
    description="Variable")
plot_example_level = widgets.Dropdown(
    options=example_batch.coords["level"].values,
    value=500,
    description="Level")
plot_example_robust = widgets.Checkbox(value=True, description="Robust")
plot_example_max_steps = widgets.IntSlider(
    min=1, max=example_batch.dims["time"], value=example_batch.dims["time"],
    description="Max steps")

widgets.VBox([
    plot_example_variable,
    plot_example_level,
    plot_example_robust,
    plot_example_max_steps,
    widgets.Label(value="Run the next cell to plot the data. Rerunning this cell clears your selection.")
])
     

CPU times: user 9.87 ms, sys: 0 ns, total: 9.87 ms
Wall time: 9.2 ms


In [9]:
# @title Plot example data

plot_size = 7

data = {
    " ": scale(select(example_batch, plot_example_variable.value, plot_example_level.value, plot_example_max_steps.value),
              robust=plot_example_robust.value),
}
fig_title = plot_example_variable.value
if "level" in example_batch[plot_example_variable.value].coords:
  fig_title += f" at {plot_example_level.value} hPa"

plot_data(data, fig_title, plot_size, plot_example_robust.value)

     

In [10]:
# @title Choose training and eval data to extract
train_steps = widgets.IntSlider(
    value=1, min=1, max=example_batch.sizes["time"]-2, description="Train steps")
eval_steps = widgets.IntSlider(
    value=example_batch.sizes["time"]-2, min=1, max=example_batch.sizes["time"]-2, description="Eval steps")

widgets.VBox([
    train_steps,
    eval_steps,
    widgets.Label(value="Run the next cell to extract the data. Rerunning this cell clears your selection.")
])

In [11]:
%%time
# @title Extract training and eval data

train_inputs, train_targets, train_forcings = data_utils.extract_inputs_targets_forcings(
    example_batch, target_lead_times=slice("6h", f"{train_steps.value*6}h"),
    **dataclasses.asdict(task_config))

eval_inputs, eval_targets, eval_forcings = data_utils.extract_inputs_targets_forcings(
    example_batch, target_lead_times=slice("6h", f"{eval_steps.value*6}h"),
    **dataclasses.asdict(task_config))

print("All Examples:  ", example_batch.dims.mapping)
print("Train Inputs:  ", train_inputs.dims.mapping)
print("Train Targets: ", train_targets.dims.mapping)
print("Train Forcings:", train_forcings.dims.mapping)
print("Eval Inputs:   ", eval_inputs.dims.mapping)
print("Eval Targets:  ", eval_targets.dims.mapping)
print("Eval Forcings: ", eval_forcings.dims.mapping)

All Examples:   {'lon': 1440, 'lat': 721, 'level': 37, 'time': 14, 'batch': 1}
Train Inputs:   {'batch': 1, 'time': 2, 'lat': 721, 'lon': 1440, 'level': 37}
Train Targets:  {'batch': 1, 'time': 1, 'lat': 721, 'lon': 1440, 'level': 37}
Train Forcings: {'batch': 1, 'time': 1, 'lat': 721, 'lon': 1440}
Eval Inputs:    {'batch': 1, 'time': 2, 'lat': 721, 'lon': 1440, 'level': 37}
Eval Targets:   {'batch': 1, 'time': 12, 'lat': 721, 'lon': 1440, 'level': 37}
Eval Forcings:  {'batch': 1, 'time': 12, 'lat': 721, 'lon': 1440}
CPU times: user 4.28 s, sys: 4.3 s, total: 8.58 s
Wall time: 8.58 s


In [12]:
%%time
# @title Load normalization data

#with gcs_bucket.blob("stats/diffs_stddev_by_level.nc").open("rb") as f:
#  diffs_stddev_by_level = xarray.load_dataset(f).compute()
#with gcs_bucket.blob("stats/mean_by_level.nc").open("rb") as f:
#  mean_by_level = xarray.load_dataset(f).compute()
#with gcs_bucket.blob("stats/stddev_by_level.nc").open("rb") as f:
#  stddev_by_level = xarray.load_dataset(f).compute()
 
with open(dl_dir + "stats/diffs_stddev_by_level.nc", "rb") as f:      
  diffs_stddev_by_level = xarray.load_dataset(f).compute()
with open(dl_dir + "stats/mean_by_level.nc", "rb") as f:
  mean_by_level = xarray.load_dataset(f).compute()
with open(dl_dir + "stats/stddev_by_level.nc", "rb") as f:
  stddev_by_level = xarray.load_dataset(f).compute()
    

CPU times: user 36.4 ms, sys: 7.82 ms, total: 44.2 ms
Wall time: 174 ms


In [13]:
%%time
# @title Build jitted functions, and possibly initialize random weights

def construct_wrapped_graphcast(
    model_config: graphcast.ModelConfig,
    task_config: graphcast.TaskConfig):
  """Constructs and wraps the GraphCast Predictor."""
  # Deeper one-step predictor.
  predictor = graphcast.GraphCast(model_config, task_config)

  # Modify inputs/outputs to `graphcast.GraphCast` to handle conversion to
  # from/to float32 to/from BFloat16.
  predictor = casting.Bfloat16Cast(predictor)

  # Modify inputs/outputs to `casting.Bfloat16Cast` so the casting to/from
  # BFloat16 happens after applying normalization to the inputs/targets.
  predictor = normalization.InputsAndResiduals(
      predictor,
      diffs_stddev_by_level=diffs_stddev_by_level,
      mean_by_level=mean_by_level,
      stddev_by_level=stddev_by_level)

  # Wraps everything so the one-step model can produce trajectories.
  predictor = autoregressive.Predictor(predictor, gradient_checkpointing=True)
  return predictor


@hk.transform_with_state
def run_forward(model_config, task_config, inputs, targets_template, forcings):
  predictor = construct_wrapped_graphcast(model_config, task_config)
  return predictor(inputs, targets_template=targets_template, forcings=forcings)


@hk.transform_with_state
def loss_fn(model_config, task_config, inputs, targets, forcings):
  predictor = construct_wrapped_graphcast(model_config, task_config)
  loss, diagnostics = predictor.loss(inputs, targets, forcings)
  return xarray_tree.map_structure(
      lambda x: xarray_jax.unwrap_data(x.mean(), require_jax=True),
      (loss, diagnostics))

def grads_fn(params, state, model_config, task_config, inputs, targets, forcings):
  def _aux(params, state, i, t, f):
    (loss, diagnostics), next_state = loss_fn.apply(
        params, state, jax.random.PRNGKey(0), model_config, task_config,
        i, t, f)
    return loss, (diagnostics, next_state)
  (loss, (diagnostics, next_state)), grads = jax.value_and_grad(
      _aux, has_aux=True)(params, state, inputs, targets, forcings)
  return loss, diagnostics, next_state, grads

# Jax doesn't seem to like passing configs as args through the jit. Passing it
# in via partial (instead of capture by closure) forces jax to invalidate the
# jit cache if you change configs.
def with_configs(fn):
  return functools.partial(
      fn, model_config=model_config, task_config=task_config)

# Always pass params and state, so the usage below are simpler
def with_params(fn):
  return functools.partial(fn, params=params, state=state)

# Our models aren't stateful, so the state is always empty, so just return the
# predictions. This is requiredy by our rollout code, and generally simpler.
def drop_state(fn):
  return lambda **kw: fn(**kw)[0]

init_jitted = jax.jit(with_configs(run_forward.init))

if params is None:
  params, state = init_jitted(
      rng=jax.random.PRNGKey(0),
      inputs=train_inputs,
      targets_template=train_targets,
      forcings=train_forcings)

loss_fn_jitted = drop_state(with_params(jax.jit(with_configs(loss_fn.apply))))
grads_fn_jitted = with_params(jax.jit(with_configs(grads_fn)))
run_forward_jitted = drop_state(with_params(jax.jit(with_configs(
    run_forward.apply))))
     

CPU times: user 1.57 ms, sys: 0 ns, total: 1.57 ms
Wall time: 1.58 ms


In [14]:
%%time
# @title Autoregressive rollout (loop in python)


assert model_config.resolution in (0, 360. / eval_inputs.sizes["lon"]), (
  "Model resolution doesn't match the data resolution. You likely want to "
  "re-filter the dataset list, and download the correct data.")

print("Inputs:  ", eval_inputs.dims.mapping)
print("Targets: ", eval_targets.dims.mapping)
print("Forcings:", eval_forcings.dims.mapping)

predictions = rollout.chunked_prediction(
    run_forward_jitted,
    rng=jax.random.PRNGKey(0),
    inputs=eval_inputs,
    targets_template=eval_targets * np.nan,
    forcings=eval_forcings)
predictions

Inputs:   {'batch': 1, 'time': 2, 'lat': 721, 'lon': 1440, 'level': 37}
Targets:  {'batch': 1, 'time': 12, 'lat': 721, 'lon': 1440, 'level': 37}
Forcings: {'batch': 1, 'time': 12, 'lat': 721, 'lon': 1440}


CPU times: user 1min 43s, sys: 8min 4s, total: 9min 47s
Wall time: 10min 20s


<xarray.Dataset>
Dimensions:                  (time: 12, batch: 1, lat: 721, lon: 1440, level: 37)
Coordinates:
  * time                     (time) timedelta64[ns] 0 days 06:00:00 ... 3 day...
  * lon                      (lon) float32 0.0 0.25 0.5 ... 359.2 359.5 359.8
  * lat                      (lat) float32 -90.0 -89.75 -89.5 ... 89.75 90.0
  * level                    (level) int32 1 2 3 5 7 10 ... 900 925 950 975 1000
Dimensions without coordinates: batch
Data variables:
    10m_u_component_of_wind  (time, batch, lat, lon) float32 -0.2521 ... 1.206
    10m_v_component_of_wind  (time, batch, lat, lon) float32 -1.146 ... -1.587
    2m_temperature           (time, batch, lat, lon) float32 248.7 ... 245.9
    geopotential             (time, batch, level, lat, lon) float32 4.93e+05 ...
    mean_sea_level_pressure  (time, batch, lat, lon) float32 9.977e+04 ... 1....
    specific_humidity        (time, batch, level, lat, lon) float32 3.904e-06...
    temperature              (time, batch, level, lat, lon) float32 284.4 ......
    total_precipitation_6hr  (time, batch, lat, lon) float32 0.0001146 ... 9....
    u_component_of_wind      (time, batch, level, lat, lon) float32 0.7283 .....
    v_component_of_wind      (time, batch, level, lat, lon) float32 -0.1536 ....
    vertical_velocity        (time, batch, level, lat, lon) float32 -0.000405...

In [15]:
%%time
# @title Choose predictions to plot

plot_pred_variable = widgets.Dropdown(
    options=predictions.data_vars.keys(),
    value="2m_temperature",
    description="Variable")
plot_pred_level = widgets.Dropdown(
    options=predictions.coords["level"].values,
    value=500,
    description="Level")
plot_pred_robust = widgets.Checkbox(value=True, description="Robust")
plot_pred_max_steps = widgets.IntSlider(
    min=1,
    max=predictions.dims["time"],
    value=predictions.dims["time"],
    description="Max steps")

widgets.VBox([
    plot_pred_variable,
    plot_pred_level,
    plot_pred_robust,
    plot_pred_max_steps,
    widgets.Label(value="Run the next cell to plot the predictions. Rerunning this cell clears your selection.")
])
   

CPU times: user 10.8 ms, sys: 3.95 ms, total: 14.8 ms
Wall time: 14.3 ms


In [ ]:
%%time
# @title Plot predictions

plot_size = 5 #5
plot_max_steps = min(predictions.dims["time"], plot_pred_max_steps.value)

data = {
    "Targets": scale(select(eval_targets, plot_pred_variable.value, plot_pred_level.value, plot_max_steps), robust=plot_pred_robust.value),
    "Predictions": scale(select(predictions, plot_pred_variable.value, plot_pred_level.value, plot_max_steps), robust=plot_pred_robust.value),
    "Diff": scale((select(eval_targets, plot_pred_variable.value, plot_pred_level.value, plot_max_steps) -
                        select(predictions, plot_pred_variable.value, plot_pred_level.value, plot_max_steps)),
                       robust=plot_pred_robust.value, center=0),
}
fig_title = plot_pred_variable.value
if "level" in predictions[plot_pred_variable.value].coords:
  fig_title += f" at {plot_pred_level.value} hPa"

plot_data(data, fig_title, plot_size, plot_pred_robust.value, 8)


CPU times: user 8.37 s, sys: 251 ms, total: 8.62 s
Wall time: 8.61 s
